# pyannotables build notebook

In [1]:
from pathlib import Path
import os
import tempfile
import urllib.request

import hvplot.pandas
import pandas as pd
import numpy as np
import pyranges as pr

from tqdm.auto import tqdm

In [2]:
def fetch_genes_and_transcripts(release=100, 
                                species='homo_sapiens',
                                build='GRCh38',
                                pub_build='',
                                release2=None,
                                datadir=Path('pyannotables') / Path('data'),
                                join_gdf=None,
                                join_tdf=None):

    if release2 is None:
        release2 = release

    gtf_url = f'http://ftp.ensembl.org/pub/{pub_build.lower()}/release-{release}/gtf/{species}/{species.capitalize()}.{build}.{release2}.chr_patch_hapl_scaff.gtf.gz'

    # download and parse ENSEMBL GTF using pyranges
    with tempfile.TemporaryDirectory() as tmpdir:
        full_path = Path(tmpdir) / 'file.gtf.gz'
        urllib.request.urlretrieve(gtf_url, full_path)
        gr = pr.read_gtf(full_path)
        
    # calculate exon lenghts of genes, which might be useful for RPKM/TPM calculations
    exon = gr[gr.Feature == 'exon'].merge(strand=True, by='gene_id').as_df()
    exon['gene_coding_length'] = exon.End - exon.Start
    exon_lengths = pd.DataFrame(exon.groupby('gene_id')['gene_coding_length'].sum())
    
    gdf = gr[gr.Feature == 'gene'][[
        'Chromosome',
        'Source',
        'Start',
        'End',
        'Strand',
        'gene_id',
        'gene_name',
        'gene_source',
        'gene_biotype',
    ]].as_df().drop_duplicates().set_index('gene_id')
    
    # add exon and gene lengths
    gdf['gene_length'] = gdf.End - gdf.Start
    gdf = gdf.join(exon_lengths)

    # join other dfs if given
    if join_gdf is not None:
        if not isinstance(join_gdf, list):
            join_gdf = [join_gdf]

        for l in join_gdf:
            gdf = gdf.join(l)

    # extract a transcript table
    tdf = gr[gr.Feature == 'transcript'][[
        'Chromosome',
        'Start',
        'End',
        'Strand',
        'gene_id',
        'transcript_id',
    ]].as_df().drop_duplicates().set_index('transcript_id')
    
    # join other dfs if given
    if join_tdf is not None:
        if not isinstance(join_tdf, list):
            join_tdf = [join_tdf]

        for l in join_tdf:
            tdf = tdf.join(l)
    
    # save everything
    datadir.mkdir(exist_ok=True)
    gdf.to_pickle(datadir / f'datafile_{species}-{build}-ensembl{release}.pkl.xz')
    tdf.to_pickle(datadir / f'datafile_{species}-{build}-ensembl{release}-tx2gene.pkl.xz')
    
    return gdf, tdf

## Human annotations

### NCBI transcript IDs

In [3]:
ncbi_df = pd.read_table('ftp://ftp.ncbi.nlm.nih.gov/gene/DATA/gene2ensembl.gz')[['#tax_id', 'GeneID', 'Ensembl_rna_identifier', 'RNA_nucleotide_accession.version']]

In [4]:
ncbi_df_human = ncbi_df[ncbi_df['#tax_id'] == 9606].copy()
ncbi_df_human = ncbi_df_human[['Ensembl_rna_identifier', 'RNA_nucleotide_accession.version']].drop_duplicates()
ncbi_df_human.columns = ['transcript_id', 'NCBI Transcript ID']
ncbi_df_human['transcript_id'] = [x.split('.')[0] for x in ncbi_df_human['transcript_id']]
ncbi_df_human.set_index('transcript_id', inplace=True)
ncbi_df_human

NCBI Transcript ID
transcript_id                     
ENST00000263100        NM_130786.4
ENST00000318602        NM_000014.6
ENST00000543404        NR_040112.1
ENST00000307719        NM_000662.8
ENST00000518029     NM_001160171.4
...                            ...
ENST00000565617        NR_164368.1
ENST00000506382     NM_001374838.1
ENST00000659509        NR_165237.1
ENST00000652788        NR_165238.1
ENST00000664509        NR_165239.1

[53883 rows x 1 columns]

### Download HGNC gene name table

In [5]:
url = 'https://www.genenames.org/cgi-bin/download/custom?col=gd_app_sym&col=gd_app_name&col=gd_status&col=gd_prev_sym&col=gd_aliases&col=gd_pub_chrom_map&col=gd_pub_ensembl_id&status=Approved&status=Entry%20Withdrawn&hgnc_dbtag=on&order_by=gd_app_sym_sort&format=text&submit=submit'
human_genes = pd.read_table(url)
human_genes = human_genes[~human_genes['Ensembl gene ID'].isnull()].set_index('Ensembl gene ID')
human_genes.rename(columns={'Chromosome': 'Chromosome_region'}, inplace=True)
human_genes

Approved symbol  \
Ensembl gene ID                   
ENSG00000121410            A1BG   
ENSG00000268895        A1BG-AS1   
ENSG00000148584            A1CF   
ENSG00000175899             A2M   
ENSG00000245105         A2M-AS1   
...                         ...   
ENSG00000162378          ZYG11B   
ENSG00000159840             ZYX   
ENSG00000274572           ZYXP1   
ENSG00000074755           ZZEF1   
ENSG00000036549            ZZZ3   

                                                     Approved name    Status  \
Ensembl gene ID                                                                
ENSG00000121410                             alpha-1-B glycoprotein  Approved   
ENSG00000268895                               A1BG antisense RNA 1  Approved   
ENSG00000148584                     APOBEC1 complementation factor  Approved   
ENSG00000175899                              alpha-2-macroglobulin  Approved   
ENSG00000245105                                A2M antisense RNA 1  Approved   
...                                                            ...       ...   
ENSG00000162378       zyg-11 family member B, cell cycle regulator  Approved   
ENSG00000159840                                              zyxin  Approved   
ENSG00000274572                                 zyxin pseudogene 1  Approved   
ENSG00000074755  zinc finger ZZ-type and EF-hand domain contain...  Approved   
ENSG00000036549                   zinc finger ZZ-type containing 3  Approved   

                            Previous symbols  \
Ensembl gene ID                                
ENSG00000121410                          NaN   
ENSG00000268895  NCRNA00181, A1BGAS, A1BG-AS   
ENSG00000148584                          NaN   
ENSG00000175899                          NaN   
ENSG00000245105                          NaN   
...                                      ...   
ENSG00000162378                        ZYG11   
ENSG00000159840                          NaN   
ENSG00000274572                          NaN   
ENSG00000074755                          NaN   
ENSG00000036549                          NaN   

                                     Alias symbols Chromosome_region  
Ensembl gene ID                                                       
ENSG00000121410                                NaN          19q13.43  
ENSG00000268895                           FLJ23569          19q13.43  
ENSG00000148584  ACF, ASP, ACF64, ACF65, APOBEC1CF          10q11.23  
ENSG00000175899             FWP007, S863-7, CPAMD5          12p13.31  
ENSG00000245105                                NaN          12p13.31  
...                                            ...               ...  
ENSG00000162378                           FLJ13456            1p32.3  
ENSG00000159840                                NaN              7q34  
ENSG00000274572                                NaN           8q24.23  
ENSG00000074755           KIAA0399, ZZZ4, FLJ10821           17p13.2  
ENSG00000036549                DKFZP564I052, ATAC1            1p31.1  

[37739 rows x 6 columns]

### GRCh38

In [6]:
species = 'homo_sapiens'

for release in tqdm((84, 93, 100)):
    gdf, tdf = fetch_genes_and_transcripts(release, species, join_gdf=human_genes, join_tdf=ncbi_df_human)
    
    display(gdf.head())
    display(tdf.head())

Chromosome   Source  Start    End Strand     gene_name  \
gene_id                                                                  
ENSG00000223972          1   havana  11868  14409      +       DDX11L1   
ENSG00000243485          1   havana  29553  31109      +  RP11-34P13.3   
ENSG00000274890          1  ensembl  30365  30503      +     MIR1302-2   
ENSG00000268020          1   havana  52472  53312      +        OR4G4P   
ENSG00000240361          1   havana  62947  63887      +       OR4G11P   

                gene_source                        gene_biotype  gene_length  \
gene_id                                                                        
ENSG00000223972      havana  transcribed_unprocessed_pseudogene         2541   
ENSG00000243485      havana                             lincRNA         1556   
ENSG00000274890     ensembl                               miRNA          138   
ENSG00000268020      havana              unprocessed_pseudogene          840   
ENSG00000240361      havana              unprocessed_pseudogene          940   

                 gene_coding_length Approved symbol  \
gene_id                                               
ENSG00000223972                1735         DDX11L1   
ENSG00000243485                1021     MIR1302-2HG   
ENSG00000274890                 138             NaN   
ENSG00000268020                 840          OR4G4P   
ENSG00000240361                 940         OR4G11P   

                                                     Approved name    Status  \
gene_id                                                                        
ENSG00000223972         DEAD/H-box helicase 11 like 1 (pseudogene)  Approved   
ENSG00000243485                                MIR1302-2 host gene  Approved   
ENSG00000274890                                                NaN       NaN   
ENSG00000268020  olfactory receptor family 4 subfamily G member...  Approved   
ENSG00000240361  olfactory receptor family 4 subfamily G member...  Approved   

                Previous symbols Alias symbols Chromosome_region  
gene_id                                                           
ENSG00000223972              NaN           NaN           1p36.33  
ENSG00000243485              NaN           NaN           1p36.33  
ENSG00000274890              NaN           NaN               NaN  
ENSG00000268020              NaN           NaN           1p36.33  
ENSG00000240361              NaN           NaN           1p36.33

Chromosome  Start    End Strand          gene_id  \
transcript_id                                                      
ENST00000456328          1  11868  14409      +  ENSG00000223972   
ENST00000450305          1  12009  13670      +  ENSG00000223972   
ENST00000473358          1  29553  31097      +  ENSG00000243485   
ENST00000469289          1  30266  31109      +  ENSG00000243485   
ENST00000607096          1  30365  30503      +  ENSG00000274890   

                NCBI Transcript ID  
transcript_id                       
ENST00000456328        NR_046018.2  
ENST00000450305                NaN  
ENST00000473358                NaN  
ENST00000469289                NaN  
ENST00000607096        NR_036051.1

Chromosome   Source  Start    End Strand    gene_name  \
gene_id                                                                 
ENSG00000223972          1   havana  11868  14409      +      DDX11L1   
ENSG00000243485          1   havana  29553  31109      +  MIR1302-2HG   
ENSG00000284332          1  mirbase  30365  30503      +    MIR1302-2   
ENSG00000268020          1   havana  52472  53312      +       OR4G4P   
ENSG00000240361          1   havana  57597  64116      +      OR4G11P   

                gene_source                        gene_biotype  gene_length  \
gene_id                                                                        
ENSG00000223972      havana  transcribed_unprocessed_pseudogene         2541   
ENSG00000243485      havana                             lincRNA         1556   
ENSG00000284332     mirbase                               miRNA          138   
ENSG00000268020      havana              unprocessed_pseudogene          840   
ENSG00000240361      havana  transcribed_unprocessed_pseudogene         6519   

                 gene_coding_length Approved symbol  \
gene_id                                               
ENSG00000223972                1735         DDX11L1   
ENSG00000243485                1021     MIR1302-2HG   
ENSG00000284332                 138       MIR1302-2   
ENSG00000268020                 840          OR4G4P   
ENSG00000240361                1414         OR4G11P   

                                                     Approved name    Status  \
gene_id                                                                        
ENSG00000223972         DEAD/H-box helicase 11 like 1 (pseudogene)  Approved   
ENSG00000243485                                MIR1302-2 host gene  Approved   
ENSG00000284332                                    microRNA 1302-2  Approved   
ENSG00000268020  olfactory receptor family 4 subfamily G member...  Approved   
ENSG00000240361  olfactory receptor family 4 subfamily G member...  Approved   

                Previous symbols   Alias symbols Chromosome_region  
gene_id                                                             
ENSG00000223972              NaN             NaN           1p36.33  
ENSG00000243485              NaN             NaN           1p36.33  
ENSG00000284332       MIRN1302-2  hsa-mir-1302-2           1p36.33  
ENSG00000268020              NaN             NaN           1p36.33  
ENSG00000240361              NaN             NaN           1p36.33

Chromosome  Start    End Strand          gene_id  \
transcript_id                                                      
ENST00000456328          1  11868  14409      +  ENSG00000223972   
ENST00000450305          1  12009  13670      +  ENSG00000223972   
ENST00000473358          1  29553  31097      +  ENSG00000243485   
ENST00000469289          1  30266  31109      +  ENSG00000243485   
ENST00000607096          1  30365  30503      +  ENSG00000284332   

                NCBI Transcript ID  
transcript_id                       
ENST00000456328        NR_046018.2  
ENST00000450305                NaN  
ENST00000473358                NaN  
ENST00000469289                NaN  
ENST00000607096        NR_036051.1

Chromosome   Source  Start    End Strand    gene_name  \
gene_id                                                                 
ENSG00000223972          1   havana  11868  14409      +      DDX11L1   
ENSG00000243485          1   havana  29553  31109      +  MIR1302-2HG   
ENSG00000284332          1  mirbase  30365  30503      +    MIR1302-2   
ENSG00000268020          1   havana  52472  53312      +       OR4G4P   
ENSG00000240361          1   havana  57597  64116      +      OR4G11P   

                gene_source                        gene_biotype  gene_length  \
gene_id                                                                        
ENSG00000223972      havana  transcribed_unprocessed_pseudogene         2541   
ENSG00000243485      havana                              lncRNA         1556   
ENSG00000284332     mirbase                               miRNA          138   
ENSG00000268020      havana              unprocessed_pseudogene          840   
ENSG00000240361      havana  transcribed_unprocessed_pseudogene         6519   

                 gene_coding_length Approved symbol  \
gene_id                                               
ENSG00000223972                1735         DDX11L1   
ENSG00000243485                1021     MIR1302-2HG   
ENSG00000284332                 138       MIR1302-2   
ENSG00000268020                 840          OR4G4P   
ENSG00000240361                1414         OR4G11P   

                                                     Approved name    Status  \
gene_id                                                                        
ENSG00000223972         DEAD/H-box helicase 11 like 1 (pseudogene)  Approved   
ENSG00000243485                                MIR1302-2 host gene  Approved   
ENSG00000284332                                    microRNA 1302-2  Approved   
ENSG00000268020  olfactory receptor family 4 subfamily G member...  Approved   
ENSG00000240361  olfactory receptor family 4 subfamily G member...  Approved   

                Previous symbols   Alias symbols Chromosome_region  
gene_id                                                             
ENSG00000223972              NaN             NaN           1p36.33  
ENSG00000243485              NaN             NaN           1p36.33  
ENSG00000284332       MIRN1302-2  hsa-mir-1302-2           1p36.33  
ENSG00000268020              NaN             NaN           1p36.33  
ENSG00000240361              NaN             NaN           1p36.33

Chromosome  Start    End Strand          gene_id  \
transcript_id                                                      
ENST00000456328          1  11868  14409      +  ENSG00000223972   
ENST00000450305          1  12009  13670      +  ENSG00000223972   
ENST00000473358          1  29553  31097      +  ENSG00000243485   
ENST00000469289          1  30266  31109      +  ENSG00000243485   
ENST00000607096          1  30365  30503      +  ENSG00000284332   

                NCBI Transcript ID  
transcript_id                       
ENST00000456328        NR_046018.2  
ENST00000450305                NaN  
ENST00000473358                NaN  
ENST00000469289                NaN  
ENST00000607096        NR_036051.1

### Gene length vs gene exon length

In [7]:
gdf.hvplot.scatter('gene_length', 'gene_coding_length', loglog=True, hover_cols=['gene_name'], c='gene_source', s=0.4, width=900, height=600)

:Scatter   [gene_length]   (gene_coding_length,gene_source,gene_name)

### GRCh37

In [8]:
release = 100
release2 = 87

gdf, tdf = fetch_genes_and_transcripts(release, species, build='GRCh37', pub_build='GRCh37', release2=release2, join_gdf=human_genes, join_tdf=ncbi_df_human)

In [9]:
gdf.head()

Chromosome          Source  Start    End Strand   gene_name  \
gene_id                                                                       
ENSG00000223972          1  ensembl_havana  11868  14412      +     DDX11L1   
ENSG00000243485          1  ensembl_havana  29553  31109      +  MIR1302-10   
ENSG00000268020          1  ensembl_havana  52472  54936      +      OR4G4P   
ENSG00000240361          1          havana  62947  63887      +     OR4G11P   
ENSG00000186092          1  ensembl_havana  69090  70008      +       OR4F5   

                    gene_source    gene_biotype  gene_length  \
gene_id                                                        
ENSG00000223972  ensembl_havana      pseudogene         2544   
ENSG00000243485  ensembl_havana         lincRNA         1556   
ENSG00000268020  ensembl_havana      pseudogene         2464   
ENSG00000240361          havana      pseudogene          940   
ENSG00000186092  ensembl_havana  protein_coding          918   

                 gene_coding_length Approved symbol  \
gene_id                                               
ENSG00000223972                1756         DDX11L1   
ENSG00000243485                1021     MIR1302-2HG   
ENSG00000268020                 947          OR4G4P   
ENSG00000240361                 940         OR4G11P   
ENSG00000186092                 918           OR4F5   

                                                     Approved name    Status  \
gene_id                                                                        
ENSG00000223972         DEAD/H-box helicase 11 like 1 (pseudogene)  Approved   
ENSG00000243485                                MIR1302-2 host gene  Approved   
ENSG00000268020  olfactory receptor family 4 subfamily G member...  Approved   
ENSG00000240361  olfactory receptor family 4 subfamily G member...  Approved   
ENSG00000186092   olfactory receptor family 4 subfamily F member 5  Approved   

                Previous symbols Alias symbols Chromosome_region  
gene_id                                                           
ENSG00000223972              NaN           NaN           1p36.33  
ENSG00000243485              NaN           NaN           1p36.33  
ENSG00000268020              NaN           NaN           1p36.33  
ENSG00000240361              NaN           NaN           1p36.33  
ENSG00000186092              NaN           NaN           1p36.33

## Mouse annotations

### Prepare NCBI transcript IDs

In [10]:
ncbi_df_mouse = ncbi_df[ncbi_df['#tax_id'] == 10090].copy()
ncbi_df_mouse = ncbi_df_mouse[['Ensembl_rna_identifier', 'RNA_nucleotide_accession.version']].drop_duplicates()
ncbi_df_mouse.columns = ['transcript_id', 'NCBI Transcript ID']
ncbi_df_mouse['transcript_id'] = [x.split('.')[0] for x in ncbi_df_mouse['transcript_id']]
ncbi_df_mouse.set_index('transcript_id', inplace=True)
ncbi_df_mouse

NCBI Transcript ID
transcript_id                        
ENSMUST00000112132        NM_007376.4
ENSMUST00000153476        NM_009591.3
ENSMUST00000021160        NR_033223.1
ENSMUST00000064307     NM_001198785.1
ENSMUST00000103019     NM_001198787.1
...                               ...
ENSMUST00000083272     XR_003956666.1
ENSMUST00000082457     XR_003956667.1
ENSMUST00000083831     XR_003956668.1
ENSMUST00000104410     XR_003956670.1
ENSMUST00000104243     XR_003956671.1

[42312 rows x 1 columns]

### GRCm38

In [11]:
gdf, tdf = fetch_genes_and_transcripts(100, 'mus_musculus', build='GRCm38', join_tdf=ncbi_df_mouse)

In [12]:
gdf.head()

Chromosome   Source    Start      End Strand  \
gene_id                                                           
ENSMUSG00000102693          1   havana  3073252  3074322      +   
ENSMUSG00000064842          1  ensembl  3102015  3102125      +   
ENSMUSG00000102851          1   havana  3252756  3253236      +   
ENSMUSG00000089699          1   havana  3466586  3513553      +   
ENSMUSG00000103147          1   havana  3531794  3532720      +   

                        gene_name gene_source          gene_biotype  \
gene_id                                                               
ENSMUSG00000102693  4933401J01Rik      havana                   TEC   
ENSMUSG00000064842        Gm26206     ensembl                 snRNA   
ENSMUSG00000102851        Gm18956      havana  processed_pseudogene   
ENSMUSG00000089699         Gm1992      havana             antisense   
ENSMUSG00000103147         Gm7341      havana  processed_pseudogene   

                    gene_length  gene_coding_length  
gene_id                                              
ENSMUSG00000102693         1070                1070  
ENSMUSG00000064842          110                 110  
ENSMUSG00000102851          480                 480  
ENSMUSG00000089699        46967                 250  
ENSMUSG00000103147          926                 926

In [13]:
tdf.head()

Chromosome    Start      End Strand             gene_id  \
transcript_id                                                                
ENSMUST00000193812          1  3073252  3074322      +  ENSMUSG00000102693   
ENSMUST00000082908          1  3102015  3102125      +  ENSMUSG00000064842   
ENSMUST00000192857          1  3252756  3253236      +  ENSMUSG00000102851   
ENSMUST00000161581          1  3466586  3513553      +  ENSMUSG00000089699   
ENSMUST00000192183          1  3531794  3532720      +  ENSMUSG00000103147   

                   NCBI Transcript ID  
transcript_id                          
ENSMUST00000193812                NaN  
ENSMUST00000082908     XR_003949180.1  
ENSMUST00000192857                NaN  
ENSMUST00000161581                NaN  
ENSMUST00000192183                NaN